In [5]:
import tensorflow as tf
import tensorflow_hub as hub # pip install --upgrade tensorflow-hub
import soundfile as sf
import requests
import numpy as np
from typing import Generator, Iterable, List, Optional
import mediapy as media #3 pip install mediapy
import os
import random
from moviepy.editor import VideoFileClip, concatenate_videoclips, AudioFileClip, ImageSequenceClip, CompositeAudioClip
import subprocess
import ffmpeg
import cv2
from pydub import AudioSegment
import gc
from numba import cuda
import torch
import multiprocessing as mp
from basicsr.archs.rrdbnet_arch import RRDBNet
from basicsr.utils.download_util import load_file_from_url
from gfpgan import GFPGANer
from realesrgan import RealESRGANer
from realesrgan.archs.srvgg_arch import SRVGGNetCompact
from moviepy.editor import VideoFileClip, concatenate_videoclips, AudioFileClip, ImageSequenceClip, CompositeAudioClip
from tqdm import tqdm

from multiprocessing import Pool



ANIME = False
SM_MODEL = True
FACE_ENHANCE = False
HD_FROM_FRAMES = True
USE_RECONSTRUCT = True





physical_devices = tf.config.list_physical_devices('GPU')
tf.config.experimental.set_memory_growth(physical_devices[0], True)


PROCCESS_BACKGROUND = False
EXCUDE_TEMPLATE_TO_PROCCESS_NAME = []
times_to_interpolate = 1
INPUT_FOLDER = "F:/gg/background/unmodded/"
PROJECT_NAME = "230313 - castle"
INPUT_FOLDER = INPUT_FOLDER + PROJECT_NAME
OUTPUT_FOLDER = 'F:/gg/background'
TEMPLATE_ANIMATION_FOLDER = 'F:\\gg\\templates\\to_proccess_ok'
TEMPLATE_ANIMATION_INTER_LQ_FOLDER = 'F:\\gg\\templates\\lq'
TEMPLATE_ANIMATION_INTER_HQ_FOLDER = 'F:\\gg\\templates\\hq'


""" hub_handle = "https://tfhub.dev/google/film/1"
hub_handle = "./film_1"
model = hub.load(hub_handle) """
_UINT8_MAX_F = float(np.iinfo(np.uint8).max)

In [6]:
def _pad_to_align(x, align):

  # Input checking.
  assert np.ndim(x) == 4
  assert align > 0, 'align must be a positive number.'

  height, width = x.shape[-3:-1]
  height_to_pad = (align - height % align) if height % align != 0 else 0
  width_to_pad = (align - width % align) if width % align != 0 else 0

  bbox_to_pad = {
      'offset_height': height_to_pad // 2,
      'offset_width': width_to_pad // 2,
      'target_height': height + height_to_pad,
      'target_width': width + width_to_pad
  }
  padded_x = tf.image.pad_to_bounding_box(x, **bbox_to_pad)
  bbox_to_crop = {
      'offset_height': height_to_pad // 2,
      'offset_width': width_to_pad // 2,
      'target_height': height,
      'target_width': width
  }
  return padded_x, bbox_to_crop

def load_image(img_url: str):  

  if (img_url.startswith("https")):
    user_agent = {'User-agent': 'Colab Sample (https://tensorflow.org)'}
    response = requests.get(img_url, headers=user_agent)
    image_data = response.content
  else:
    image_data = tf.io.read_file(img_url)

  image = tf.io.decode_image(image_data, channels=3)
  image_numpy = tf.cast(image, dtype=tf.float32) #.numpy()
  image_numpy = tf.image.resize(
    images=image_numpy,
    # size=[HEIGHT, WIDTH],
    size=[270, 480],
    method=tf.image.ResizeMethod.BILINEAR,
    preserve_aspect_ratio=False,
    antialias=True,
    ).numpy()
  """ image_numpy = np.clip(image_numpy, 0, 255)  """
  return image_numpy / _UINT8_MAX_F

class Interpolator:
  physical_devices = tf.config.list_physical_devices('GPU')
  tf.config.experimental.set_memory_growth(physical_devices[0], True)
  def __init__(self, align: int = 64) -> None:

    #self._model = hub.load("https://tfhub.dev/google/film/1")
    self._model = hub.load(".\\film_1")
    self._align = align

  def __call__(self, x0: np.ndarray, x1: np.ndarray,
               dt: np.ndarray) -> np.ndarray:

    if self._align is not None:
      x0, bbox_to_crop = _pad_to_align(x0, self._align)
      x1, _ = _pad_to_align(x1, self._align)

    inputs = {'x0': x0, 'x1': x1, 'time': dt[..., np.newaxis]}
    result = self._model(inputs, training=False)
    image = result['image']

    if self._align is not None:
      image = tf.image.crop_to_bounding_box(image, **bbox_to_crop)
    return image.numpy()

def _recursive_generator(
    frame1: np.ndarray, frame2: np.ndarray, num_recursions: int,
    interpolator: Interpolator) -> Generator[np.ndarray, None, None]:

  if num_recursions == 0:
    yield frame1
  else:
    # Adds the batch dimension to all inputs before calling the interpolator,
    # and remove it afterwards.
    time = np.full(shape=(1,), fill_value=0.5, dtype=np.float32)
    mid_frame = interpolator(
        np.expand_dims(frame1, axis=0), np.expand_dims(frame2, axis=0), time)[0]
    yield from _recursive_generator(frame1, mid_frame, num_recursions - 1,
                                    interpolator)
    yield from _recursive_generator(mid_frame, frame2, num_recursions - 1,
                                    interpolator)

def interpolate_recursively(
    frames: List[np.ndarray], num_recursions: int,
    interpolator: Interpolator) -> Iterable[np.ndarray]:

  n = len(frames)
  for i in range(1, n):
    yield from _recursive_generator(frames[i - 1], frames[i],
                                    times_to_interpolate, interpolator)
  # Separately yield the final frame.
  yield frames[-1]

def get_all_files(folder):
  temp_array = []
  for filename in os.listdir(folder):
      temp_array.append(f"{folder}//{filename}")
  return temp_array


def concat_videos(videos, output_path):
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    frame_width = 0
    frame_height = 0
    frame_count = 0
    audio_segments = []
    video_list = []

    for video in videos:
        cap = cv2.VideoCapture(video)
        frame_width = int(cap.get(3))
        frame_height = int(cap.get(4))
        frame_count += int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
        video_list.append(cap)
        audio = AudioSegment.from_file(video, "mp4")
        audio_segments.append(audio)

    out = cv2.VideoWriter(output_path, fourcc, 20.0, (frame_width, frame_height))
    frame_index = 0

    while True:
        finished = True
        for cap in video_list:
            if cap.isOpened():
                finished = False
                ret, frame = cap.read()
                if ret == True:
                    out.write(frame)
                    frame_index += 1
                else:
                    cap.release()

        if finished or frame_index >= frame_count:
            break

    out.release()
    cv2.destroyAllWindows()

    final_audio = AudioSegment.silent(duration=0)
    for audio in audio_segments:
        final_audio += audio

    final_audio.export(output_path.replace(".mp4", ".wav"), format="wav")

interpolator = Interpolator()

def load_images_from_folder(folder_path):
    images = []
    for filename in os.listdir(folder_path):
        if filename.endswith('.png'):
            img_url = os.path.join(folder_path, filename)
            image_data = tf.io.read_file(img_url)
            image = tf.io.decode_image(image_data, channels=3)
            image_numpy = tf.cast(image, dtype=tf.float32) #.numpy()
            """             image_numpy = tf.image.resize(
                images=image_numpy,
                size=[270, 480],
                method=tf.image.ResizeMethod.BILINEAR,
                preserve_aspect_ratio=False,
                antialias=True,
            ).numpy() """
            images.append(image_numpy / _UINT8_MAX_F)
    return images

netscale = 4
model_path_face = "./realesrgan/GFPGANv1.3.pth"
dni_weight = None
tile = 0
title_pad = 10
pre_pad = 0
half = None
gpu_id = None
upscale = 4
img_mode = 'RGBA'

print(f"Face Enhance = {FACE_ENHANCE}")

if ANIME:  
    if not SM_MODEL:
      print('loading anime 4x')
      model = RRDBNet(num_in_ch=3, num_out_ch=3, num_feat=64, num_block=6, num_grow_ch=32, scale=4)
      model_path_x4 = "./realesrgan/RealESRGAN_x4plus_anime_6B.pth"
      """ else:
      # R-ESRGAN
      model = RRDBNet(num_in_ch=3, num_out_ch=3, num_feat=64, num_block=23, num_grow_ch=32, scale=4)
      model_path_x4 = "./realesrgan/RealESRGAN_x4plus.pth" """

      upsampler = RealESRGANer(
              scale=netscale,
              model_path=model_path_x4,
              dni_weight=dni_weight,
              model=model,
              tile=tile,
              tile_pad=title_pad,
              pre_pad=pre_pad,
              half= not half,
              gpu_id= gpu_id
      )

      face_enhancer = GFPGANer(
                  model_path=model_path_face,
                  upscale=upscale,
                  arch='clean',
                  channel_multiplier=2,
                  bg_upsampler=upsampler)
    else:
      print('loading anime 2x')
      model = SRVGGNetCompact(num_in_ch=3, num_out_ch=3, num_feat=64, num_conv=16, upscale=4, act_type='prelu')
      model_path_x2 = "./realesrgan/realesr-animevideov3.pth"
      upsampler = RealESRGANer(
        scale=netscale,
        model_path=model_path_x2,
        dni_weight=dni_weight,
        model=model,
        tile=tile,
        tile_pad=title_pad,
        pre_pad=pre_pad,
        half= not half,
        gpu_id= gpu_id
      )

      """ from gfpgan import GFPGANer """
      face_enhancer = GFPGANer(
                  model_path=model_path_face,
                  upscale=upscale,
                  arch='clean',
                  channel_multiplier=2,
                  bg_upsampler=upsampler)
        
else:
  if not SM_MODEL:
    print('loading real HD')
    from basicsr.archs.rrdbnet_arch import RRDBNet
    arch = 'clean'
    channel_multiplier = 2
    model_name = 'GFPGANv1.4'
    url = 'https://github.com/TencentARC/GFPGAN/releases/download/v1.3.0/GFPGANv1.4.pth'
    model_path = os.path.join('./gfpgan/gfpgan/weights', model_name + '.pth')
    model = RRDBNet(num_in_ch=3, num_out_ch=3, num_feat=64, num_block=23, num_grow_ch=32, scale=2)
    upsampler = RealESRGANer(
              scale=2,
              model_path='https://github.com/xinntao/Real-ESRGAN/releases/download/v0.2.1/RealESRGAN_x2plus.pth',
              model=model,
              tile=400,
              tile_pad=10,
              pre_pad=0,
              half=True)  # need to set False in CPU mode

    face_enhancer = GFPGANer(
      model_path=model_path,
      upscale=upscale,
      arch=arch,
      channel_multiplier=channel_multiplier,
      bg_upsampler=upsampler)

  else: 
    print('loading real SM')
    model = SRVGGNetCompact(num_in_ch=3, num_out_ch=3, num_feat=64, num_conv=32, upscale=4, act_type='prelu')
    file_url = [
            'https://github.com/xinntao/Real-ESRGAN/releases/download/v0.2.5.0/realesr-general-wdn-x4v3.pth',
            'https://github.com/xinntao/Real-ESRGAN/releases/download/v0.2.5.0/realesr-general-x4v3.pth'
    ]
    model_path = os.path.join('weights', 'realesr-general-x4v3' + '.pth')
    if not os.path.isfile(model_path):
        ROOT_DIR = os.path.dirname(os.path.abspath(__file__))
        for url in file_url:
            # model_path will be updated
            model_path = load_file_from_url(
                url=url, model_dir=os.path.join(ROOT_DIR, 'weights'), progress=True, file_name=None)
  
    wdn_model_path = model_path.replace('realesr-general-x4v3', 'realesr-general-wdn-x4v3')
    model_path = [model_path, wdn_model_path]
    dni_weight = [0.5, 1 - 0.5]
    
    upsampler = RealESRGANer(
        scale=netscale,
        model_path=model_path,
        dni_weight=dni_weight,
        model=model,
        tile=tile,
        tile_pad=title_pad,
        pre_pad=pre_pad,
        half= not half,
        gpu_id= gpu_id
    )


    from gfpgan import GFPGANer
    face_enhancer = GFPGANer(
        model_path=model_path_face,
        upscale=upscale,
        arch='clean',
        channel_multiplier=2,
        bg_upsampler=upsampler)

def subprocess():
    print('inside!')
    """ try:
      # Allocate GPU memory
      gpus = tf.config.experimental.list_physical_devices('GPU')
      tf.config.experimental.set_memory_growth(gpus[0], True)

      # Load model
      interpolator = Interpolator()

      # Perform image processing using the model
      if (not os.path.exists(TEMPLATE_ANIMATION_INTER_LQ_FOLDER)):
          os.makedirs(TEMPLATE_ANIMATION_INTER_LQ_FOLDER)
      for folder_name in os.listdir(f'{TEMPLATE_ANIMATION_FOLDER}\\{TEMPLATE_TO_PROCCESS_NAME}'):
          input_frames = load_images_from_folder(f'{TEMPLATE_ANIMATION_FOLDER}\\{TEMPLATE_TO_PROCCESS_NAME}\\{folder_name}')

          frames = list(
              interpolate_recursively(input_frames, times_to_interpolate,
                                                  interpolator))
          
          # frames = [np.clip(np.array(img)*255,0, 255) for img in frames]
          if (not os.path.exists(f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}")):
              os.makedirs(f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}")
          for i, single_frame in enumerate(frames):
              media.write_image(f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}/output_{i:04d}.png", single_frame)
          media.show_video(frames, fps=30, title='FILM interpolated video')
    except Exception as e:
      print("Exception caught in subprocess:", e) """
    # End subprocess
    return

In [7]:
""" frame_count = 0
for i, filename in enumerate(os.listdir(INPUT_FOLDER)):
    img = cv2.imread(f"{INPUT_FOLDER}/{filename}",cv2.IMREAD_UNCHANGED)
    img = cv2.resize(img,(1920,1080))
    cv2.imwrite(f"{OUTPUT_FOLDER}/output_{frame_count:04d}.png", img)
    frame_count += 1
    cv2.imwrite(f"{OUTPUT_FOLDER}/output_{frame_count:04d}.png", img)
    frame_count += 1
 """

' frame_count = 0\nfor i, filename in enumerate(os.listdir(INPUT_FOLDER)):\n    img = cv2.imread(f"{INPUT_FOLDER}/{filename}",cv2.IMREAD_UNCHANGED)\n    img = cv2.resize(img,(1920,1080))\n    cv2.imwrite(f"{OUTPUT_FOLDER}/output_{frame_count:04d}.png", img)\n    frame_count += 1\n    cv2.imwrite(f"{OUTPUT_FOLDER}/output_{frame_count:04d}.png", img)\n    frame_count += 1\n '

In [8]:
if PROCCESS_BACKGROUND:
    print('later')
else:

    if (not os.path.exists(TEMPLATE_ANIMATION_INTER_LQ_FOLDER)):
        os.makedirs(TEMPLATE_ANIMATION_INTER_LQ_FOLDER)
    for folder_project in os.listdir(f'{TEMPLATE_ANIMATION_FOLDER}'):
        if folder_project not in EXCUDE_TEMPLATE_TO_PROCCESS_NAME:
            TEMPLATE_TO_PROCCESS_NAME = folder_project
            print(folder_project)
            for folder_name in tqdm(os.listdir(f'{TEMPLATE_ANIMATION_FOLDER}\\{TEMPLATE_TO_PROCCESS_NAME}')):
                if folder_name[-3:] != 'txt':
                    if (not os.path.exists(f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}")):
                        os.makedirs(f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}")
                        input_frames = load_images_from_folder(f'{TEMPLATE_ANIMATION_FOLDER}\\{TEMPLATE_TO_PROCCESS_NAME}\\{folder_name}')

                        frames = list(
                            interpolate_recursively(input_frames, times_to_interpolate,
                                                                interpolator))
                        
                        # frames = [np.clip(np.array(img)*255,0, 255) for img in frames]
                        
                        for i, single_frame in enumerate(frames):
                            media.write_image(f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}/output_{i:04d}.png", single_frame)
                        # media.show_video(frames, fps=30, title='FILM interpolated video')
    tf.compat.v1.reset_default_graph()
    tf.keras.backend.clear_session()
    gc.collect()


    if (not os.path.exists(TEMPLATE_ANIMATION_INTER_HQ_FOLDER)):
        os.makedirs(TEMPLATE_ANIMATION_INTER_HQ_FOLDER)
    for folder_project in os.listdir(f'{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}'):
            if folder_project not in EXCUDE_TEMPLATE_TO_PROCCESS_NAME:
                TEMPLATE_TO_PROCCESS_NAME = folder_project
                print(folder_project)
                for folder_name in tqdm(os.listdir(f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}")):
                    if (not os.path.exists(f"{TEMPLATE_ANIMATION_INTER_HQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}")):
                        os.makedirs(f"{TEMPLATE_ANIMATION_INTER_HQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}")
                        for j, frame_lq in enumerate(os.listdir(f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}")):
                            img_path = f"{TEMPLATE_ANIMATION_INTER_LQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}/{frame_lq}"
                            img = cv2.imread(img_path, cv2.IMREAD_UNCHANGED)

                            if USE_RECONSTRUCT:
                                if FACE_ENHANCE:                    
                                    _, _, output = face_enhancer.enhance(img, has_aligned=False, only_center_face=False, paste_back=True)
                                else:
                                    output, _ = upsampler.enhance(img, outscale=upscale)
                            else:
                                output = cv2.addWeighted(img, 1 + 5/127, img, 0, 10 - 5)   
                            output = cv2.resize(output, (1920, 1080))
                            cv2.imwrite(f"{TEMPLATE_ANIMATION_INTER_HQ_FOLDER}/{TEMPLATE_TO_PROCCESS_NAME}/{folder_name}/{frame_lq}", output)
    torch.cuda.empty_cache()
    gc.collect()
  

F:\gg\templates\to_proccess\a globe inside a jar
video with 239 frames


FILM interpolated video This browser does not support the video tag.


F:\gg\templates\to_proccess\a globe inside a jar
video with 239 frames


FILM interpolated video This browser does not support the video tag.
